In [1]:
!pip install openai==0.28

  Obtaining dependency information for openai==0.28 from https://files.pythonhosted.org/packages/ae/59/911d6e5f1d7514d79c527067643376cddcf4cb8d1728e599b3b03ab51c69/openai-0.28.0-py3-none-any.whl.metadata
  Using cached openai-0.28.0-py3-none-any.whl.metadata (13 kB)
Using cached openai-0.28.0-py3-none-any.whl (76 kB)
  Attempting uninstall: openai
    Found existing installation: openai 1.35.3
    Uninstalling openai-1.35.3:
      Successfully uninstalled openai-1.35.3


In [2]:
import pandas as pd
import re

In [4]:

df = pd.read_csv('gap_sample_data2.csv')



In [5]:
df.head()

SKU_number   headline  rating  \
0      100001      Jeans       5   
1      100001  Run small       1   
2      100001  Love them       5   
3      100001  Good buy!       5   
4      100001        Fit       5   

                                            comments          Dept  
0                                 New favorite jeans  WOMENS DENIM  
1  Run 2 sizes too small.  Tons of old navy.. alw...  WOMENS DENIM  
2  I love they are a little heavy and they keep y...  WOMENS DENIM  
3        Size was correct, good value for the price!  WOMENS DENIM  
4  Best jeans.  Perfect fit!! Love them.  Will de...  WOMENS DENIM

In [6]:
def clean_comments(text):
    # Remove alphanumeric characters
    cleaned_text = re.sub(r'\b\w*\d+\w*\b', '', text)
    # Remove extra spaces
    cleaned_text = re.sub(r'\s+', ' ', cleaned_text).strip()
    return cleaned_text

# Apply the cleaning function to the comments column
df['comments'] = df['comments'].apply(clean_comments)

# Drop rows where cleaned_comments is empty 
df = df[df['comments'].str.strip().astype(bool)]



In [7]:
df

SKU_number               headline  rating  \
0       100001                  Jeans       5   
1       100001              Run small       1   
2       100001              Love them       5   
3       100001              Good buy!       5   
4       100001                    Fit       5   
..         ...                    ...     ...   
69      100004    Great fitting jeans       5   
70      100004             Nice jeans       4   
71      100004  Trendy & comfortable!       5   
72      100004               Perfect!       5   
73      100004             No stretch       2   

                                             comments          Dept  
0                                  New favorite jeans  WOMENS DENIM  
1   Run sizes too small. Tons of old navy.. always...  WOMENS DENIM  
2   I love they are a little heavy and they keep y...  WOMENS DENIM  
3         Size was correct, good value for the price!  WOMENS DENIM  
4   Best jeans. Perfect fit!! Love them. Will defi...  WOMENS DENIM  
..                                                ...           ...  
69  I love these jeans. They are not too tight and...  WOMENS DENIM  
70                             snug at waist for size  WOMENS DENIM  
71                 Very flattering, love the stretch!  WOMENS DENIM  
72  Love these jeans! They're the perfect rise and...  WOMENS DENIM  
73          These jeans were long and had no stretch.  WOMENS DENIM  

[74 rows x 5 columns]

In [8]:
import openai
openai.api_type = "azure"
openai.api_base = "https://mockalbertsonproject1.openai.azure.com/"  
openai.api_version = "2023-03-15-preview" 
openai.api_key = 'c4ee8058643346adb47e00b70a116c83'

In [9]:
import requests
import json
import time

def azure_text_model(prompt):
    """
    Model: GPT-3.5-turbo on Azure OpenAI
    """
    # Reading API_KEY and Endpoints using config
    sleep_time = 0

    API_KEY = "c4ee8058643346adb47e00b70a116c83"
    endpoint = "https://mockalbertsonproject1.openai.azure.com/openai/deployments/GAPllm/chat/completions?api-version=2024-02-15-preview"

    headers = {  
        "Content-Type": "application/json",
        "api-key": API_KEY
    }
    
    # Prepare endpoint, headers, and request body  
    data = {
        "messages": [
            {"role": "system", "content": "You are an assistant that analyzes customer comments for product reviews."},
            {"role": "user", "content": prompt}
        ],
        "max_tokens": 1000,
        "temperature": 0.7
    }

    start = time.time()
    # Make the API call
    try:
        response = requests.post(endpoint, headers=headers, data=json.dumps(data))
        result = response.json()
        status = response.status_code

    except Exception as e:
        print(e)
        status = 404
        result = {}

    if status == 429:
        try:
            retry_match = re.search(r'retry after (\d+) ', result['error']['message'], re.IGNORECASE)
            print(retry_match.group(1))
            sleep_time = int(retry_match.group(1))
        
        except:
            print('Not able to extract waiting seconds')
            sleep_time = 20

    return status, sleep_time, result


In [10]:
def analyze_sentiment(comment):
    prompt = f"""Analyze the following comment in short and provide sentiment scores for the categories: silhouette, proportion_or_fit, detail, color, print_or_pattern, and fabric. The sentiment scores should be 1 if the customer likes it, -1 if the customer dislikes it, and 0 if no comments are made about that attribute.

    Comment: "{comment}"

    Format the response as follows:
    silhouette: [sentiment]
    silhouette mapping: [reason]
    proportion_or_fit: [sentiment]
    proportion_or_fit mapping: [reason]
    detail: [sentiment]
    detail mapping: [reason]
    color: [sentiment]
    color mapping: [reason]
    print_or_pattern: [sentiment]
    print_or_pattern mapping: [reason]
    fabric: [sentiment]
    fabric mapping: [reason]
    """

    status, sleep_time, result = azure_text_model(prompt)
    
    if status == 200:
        response_text = result['choices'][0]['message']['content'].strip()
        
        # Parsing the response
        parsed_result = {}
        for line in response_text.split("\n"):
            if line:
                key, value = line.split(": ")
                parsed_result[key.strip()] = value.strip()
        
        return parsed_result
    else:
        print(f"Error: {result}")
        return {}

In [11]:
categories = ["silhouette", "proportion_or_fit", "detail", "color", "print_or_pattern", "fabric"]
for category in categories:
    df[f"{category}"] = 0
    df[f"{category} mapping"] = "NA"


for index, row in df.iterrows():
    sentiment_analysis = analyze_sentiment(row['comments'])
    if sentiment_analysis:
        for category in categories:
            sentiment_key = f"{category}"
            mapping_key = f"{category} mapping"
            if sentiment_key in sentiment_analysis and mapping_key in sentiment_analysis:
                try:
                    df.at[index, sentiment_key] = int(sentiment_analysis[sentiment_key])
                except ValueError:
                    print("Invalid value for {}: {}".format(sentiment_key, sentiment_analysis[sentiment_key]))
                    df.at[index, sentiment_key] = 0  
                df.at[index, mapping_key] = sentiment_analysis[mapping_key]
            else:
                print("Missing key {} or {} in the response for comment: {}".format(sentiment_key, mapping_key, row['comments']))



Missing key detail or detail mapping in the response for comment: These are perfectly cropped for my height! Not skinny tight but also not too loose - the best casual jeans to go with sneaks, a cute heal or even birks. Love them so much I ordered another pair.
Missing key color or color mapping in the response for comment: These are perfectly cropped for my height! Not skinny tight but also not too loose - the best casual jeans to go with sneaks, a cute heal or even birks. Love them so much I ordered another pair.
Missing key print_or_pattern or print_or_pattern mapping in the response for comment: These are perfectly cropped for my height! Not skinny tight but also not too loose - the best casual jeans to go with sneaks, a cute heal or even birks. Love them so much I ordered another pair.


In [13]:
df

SKU_number               headline  rating  \
0       100001                  Jeans       5   
1       100001              Run small       1   
2       100001              Love them       5   
3       100001              Good buy!       5   
4       100001                    Fit       5   
..         ...                    ...     ...   
69      100004    Great fitting jeans       5   
70      100004             Nice jeans       4   
71      100004  Trendy & comfortable!       5   
72      100004               Perfect!       5   
73      100004             No stretch       2   

                                             comments          Dept  \
0                                  New favorite jeans  WOMENS DENIM   
1   Run sizes too small. Tons of old navy.. always...  WOMENS DENIM   
2   I love they are a little heavy and they keep y...  WOMENS DENIM   
3         Size was correct, good value for the price!  WOMENS DENIM   
4   Best jeans. Perfect fit!! Love them. Will defi...  WOMENS DENIM   
..                                                ...           ...   
69  I love these jeans. They are not too tight and...  WOMENS DENIM   
70                             snug at waist for size  WOMENS DENIM   
71                 Very flattering, love the stretch!  WOMENS DENIM   
72  Love these jeans! They're the perfect rise and...  WOMENS DENIM   
73          These jeans were long and had no stretch.  WOMENS DENIM   

    silhouette                                 silhouette mapping  \
0            0                   No comment made about silhouette   
1            0                  No comments made about silhouette   
2            0                                    No comment made   
3            0                                No comment provided   
4            0                   No comment made about silhouette   
..         ...                                                ...   
69           1  The customer likes the silhouette and fit of t...   
70           0               No specific comment about silhouette   
71           1  The customer finds the silhouette very flatter...   
72           0                                    No comment made   
73           0          No specific comment about the silhouette.   

    proportion_or_fit                          proportion_or_fit mapping  \
0                   1                             Customer likes the fit   
1                  -1                          Customer dislikes the fit   
2                   0                                    No comment made   
3                   1            The customer is satisfied with the size   
4                   1                             Customer likes the fit   
..                ...                                                ...   
69                  1  The customer finds the fit of the jeans to be ...   
70                 -1        Customer dislikes the snug fit at the waist   
71                  1     The customer loves the stretch of the product.   
72                  1                    Customer likes the rise and fit   
73                 -1  The customer dislikes the fit, mentioning that...   

    detail                                     detail mapping  color  \
0        0                       No comment made about detail      0   
1        0                      No comments made about detail      0   
2        0                                    No comment made      0   
3        0                                No comment provided      0   
4        0                       No comment made about detail      0   
..     ...                                                ...    ...   
69       0  No specific comments about the details of the ...      0   
70       0                   No specific comment about detail      0   
71       0        No specific comments made about the detail.      0   
72       1        Customer likes the durability and thickness      0   
73       0             No sp

In [14]:
import openai

In [15]:
def get_embedding(text, model="embeddingsharepoint"):
    response = openai.Embedding.create(
        engine=model,
        input=text
    )
    return response['data'][0]['embedding']



In [16]:
df['embedding'] = df['comments'].apply(lambda x: get_embedding(x))
df

SKU_number               headline  rating  \
0       100001                  Jeans       5   
1       100001              Run small       1   
2       100001              Love them       5   
3       100001              Good buy!       5   
4       100001                    Fit       5   
..         ...                    ...     ...   
69      100004    Great fitting jeans       5   
70      100004             Nice jeans       4   
71      100004  Trendy & comfortable!       5   
72      100004               Perfect!       5   
73      100004             No stretch       2   

                                             comments          Dept  \
0                                  New favorite jeans  WOMENS DENIM   
1   Run sizes too small. Tons of old navy.. always...  WOMENS DENIM   
2   I love they are a little heavy and they keep y...  WOMENS DENIM   
3         Size was correct, good value for the price!  WOMENS DENIM   
4   Best jeans. Perfect fit!! Love them. Will defi...  WOMENS DENIM   
..                                                ...           ...   
69  I love these jeans. They are not too tight and...  WOMENS DENIM   
70                             snug at waist for size  WOMENS DENIM   
71                 Very flattering, love the stretch!  WOMENS DENIM   
72  Love these jeans! They're the perfect rise and...  WOMENS DENIM   
73          These jeans were long and had no stretch.  WOMENS DENIM   

    silhouette                                 silhouette mapping  \
0            0                   No comment made about silhouette   
1            0                  No comments made about silhouette   
2            0                                    No comment made   
3            0                                No comment provided   
4            0                   No comment made about silhouette   
..         ...                                                ...   
69           1  The customer likes the silhouette and fit of t...   
70           0               No specific comment about silhouette   
71           1  The customer finds the silhouette very flatter...   
72           0                                    No comment made   
73           0          No specific comment about the silhouette.   

    proportion_or_fit                          proportion_or_fit mapping  \
0                   1                             Customer likes the fit   
1                  -1                          Customer dislikes the fit   
2                   0                                    No comment made   
3                   1            The customer is satisfied with the size   
4                   1                             Customer likes the fit   
..                ...                                                ...   
69                  1  The customer finds the fit of the jeans to be ...   
70                 -1        Customer dislikes the snug fit at the waist   
71                  1     The customer loves the stretch of the product.   
72                  1                    Customer likes the rise and fit   
73                 -1  The customer dislikes the fit, mentioning that...   

    detail                                     detail mapping  color  \
0        0                       No comment made about detail      0   
1        0                      No comments made about detail      0   
2        0                                    No comment made      0   
3        0                                No comment provided      0   
4        0                       No comment made about detail      0   
..     ...                                                ...    ...   
69       0  No specific comments about the details of the ...      0   
70       0                   No specific comment about detail      0   
71       0        No specific comments made about the detail.      0   
72       1        Customer likes the durability and thickness      0   
73       0             No sp

In [112]:
grouped_df = df.groupby('headline').agg(lambda x: x.tolist()).reset_index()

In [113]:
data_json = df.to_dict(orient='records')
data_json

[{'SKU_number': 100001,
  'headline': 'Jeans',
  'rating': 5,
  'comments': 'New favorite jeans',
  'Dept': 'WOMENS DENIM',
  'silhouette': 0,
  'silhouette mapping': 'No specific comment made about the silhouette.',
  'proportion_or_fit': 1,
  'proportion_or_fit mapping': 'The customer likes the fit of the jeans.',
  'detail': 0,
  'detail mapping': 'No specific comment made about the details.',
  'color': 0,
  'color mapping': 'No specific comment made about the color.',
  'print_or_pattern': 0,
  'print_or_pattern mapping': 'No specific comment made about print or pattern.',
  'fabric': 0,
  'fabric mapping': 'No specific comment made about the fabric.',
  'embedding': [-0.025679241865873337,
   -0.010862798430025578,
   -0.002501813927665353,
   -0.019210821017622948,
   -0.022257070988416672,
   0.01624234765768051,
   -0.017629362642765045,
   -0.03870682045817375,
   0.0025082954671233892,
   -0.022944098338484764,
   0.01644975133240223,
   0.0010572756873443723,
   -0.00252287

In [123]:
from azure.cosmos import CosmosClient, PartitionKey
import uuid
# Your Cosmos DB credentials
url = "https://gapcosmosdbprlnj01.documents.azure.com:443/"
key = "001c6Nscqk9nmVP1dLzlmZ3RMpAchSayxUOfpu4BKcr1tUkR486TCtUhdCnwyjJMiFsNTkEpZD6CACDbdYfNIQ=="
database_name = "gapprojectdatabase"
container_name = "gapprojectcontainer1"
    

# Initialize the Cosmos client
client = CosmosClient(url, credential=key)

# Create a database and a container if they don't exist
database = client.create_database_if_not_exists(id=database_name)
container = database.create_container_if_not_exists(
    id=container_name,
    partition_key=PartitionKey(path='/headline'),  
    offer_throughput=400
)

for data in data_json:
    data['id'] = str(uuid.uuid4())  # Generate a unique id
    container.create_item(body=data)

print("Data inserted successfully")

Data inserted successfully


In [36]:
import pandas as pd
import requests

API_KEY = "c4ee8058643346adb47e00b70a116c83"
ENDPOINT = "https://mockalbertsonproject1.openai.azure.com"
MODEL = "gapllm2"
API_VERSION = "2023-03-15-preview"

def summarize_comment(comment):
    prompt = f"Summarize the following review in short only: {comment}"
    headers = {
        'Content-Type': 'application/json',
        'api-key': API_KEY,
    }
    data = {
        'messages': [
            {'role': 'system', 'content': 'You are a helpful assistant.'},
            {'role': 'user', 'content': prompt}
        ],
        'max_tokens': 50,
        'temperature': 0.7,
    }
    
    try:
        response = requests.post(f"{ENDPOINT}/openai/deployments/{MODEL}/chat/completions?api-version={API_VERSION}", headers=headers, json=data)
        response.raise_for_status()
        response_data = response.json()
        summary = response_data.get('choices', [{}])[0].get('message', {}).get('content', 'No summary available')
        return summary
    except requests.exceptions.HTTPError as e:
        print(f"HTTP error occurred: {e}")
        print(f"Response content: {response.text}")
        return "Error: Unable to summarize comment"
    except Exception as e:
        print(f"An error occurred: {e}")
        return "Error: Unable to summarize comment"

In [38]:
def classify_sentiment(comment):
    prompt = f"Classify the sentiment of the following review as positive, neutral, or negative: {comment}"
    headers = {
        'Content-Type': 'application/json',
        'api-key': API_KEY,
    }
    data = {
        'messages': [
            {'role': 'system', 'content': 'You are a helpful assistant.'},
            {'role': 'user', 'content': prompt}
        ],
        'max_tokens': 50,
        'temperature': 0.7,
    }
    response = requests.post(f"{ENDPOINT}/openai/deployments/{MODEL}/chat/completions?api-version={API_VERSION}", headers=headers, json=data)
    response_data = response.json()
    
    sentiment = response_data['choices'][0]['message']['content'].strip().lower()
    
    if 'positive' in sentiment:
        return 1
    elif 'negative' in sentiment:
        return -1
    else:
        return 0



In [34]:

df['summary'] = df['comments'].apply(summarize_comment)



HTTP error occurred: 400 Client Error: model_error for url: https://mockalbertsonproject1.openai.azure.com/openai/deployments/gapllm2/chat/completions?api-version=2023-03-15-preview
Response content: {"error":{"message":"The response was filtered due to the prompt triggering Azure OpenAI's content management policy. Please modify your prompt and retry. To learn more about our content filtering policies please read our documentation: https://go.microsoft.com/fwlink/?linkid=2198766","type":null,"param":"prompt","code":"content_filter","status":400}}
    SKU_number               headline  rating  \
0       100001                  Jeans       5   
1       100001              Run small       1   
2       100001              Love them       5   
3       100001              Good buy!       5   
4       100001                    Fit       5   
..         ...                    ...     ...   
69      100004    Great fitting jeans       5   
70      100004             Nice jeans       4   
71   

In [39]:
df['sentiment'] = df['summary'].apply(classify_sentiment)

In [40]:
df.head()

SKU_number   headline  rating  \
0      100001      Jeans       5   
1      100001  Run small       1   
2      100001  Love them       5   
3      100001  Good buy!       5   
4      100001        Fit       5   

                                            comments          Dept  \
0                                 New favorite jeans  WOMENS DENIM   
1  Run sizes too small. Tons of old navy.. always...  WOMENS DENIM   
2  I love they are a little heavy and they keep y...  WOMENS DENIM   
3        Size was correct, good value for the price!  WOMENS DENIM   
4  Best jeans. Perfect fit!! Love them. Will defi...  WOMENS DENIM   

   silhouette                 silhouette mapping  proportion_or_fit  \
0           0   No comment made about silhouette                  1   
1           0  No comments made about silhouette                 -1   
2           0                    No comment made                  0   
3           0                No comment provided                  1   
4           0   No comment made about silhouette                  1   

                 proportion_or_fit mapping  detail  \
0                   Customer likes the fit       0   
1                Customer dislikes the fit       0   
2                          No comment made       0   
3  The customer is satisfied with the size       0   
4                   Customer likes the fit       0   

                  detail mapping  color                 color mapping  \
0   No comment made about detail      0   No comment made about color   
1  No comments made about detail      0  No comments made about color   
2                No comment made      0               No comment made   
3            No comment provided      0           No comment provided   
4   No comment made about detail      0   No comment made about color   

   print_or_pattern                 print_or_pattern mapping  fabric  \
0                 0   No comment made about print or pattern       0   
1                 0  No comments made about print or pattern       0   
2                 0                          No comment made       1   
3                 0                      No comment provided       1   
4                 0   No comment made about print or pattern       0   

                                      fabric mapping  \
0                       No comment made about fabric   
1                      No comments made about fabric   
2             Customer likes that it keeps them warm   
3  The customer finds it to be a good value for t...   
4                       No comment made about fabric   

                                           embedding  \
0  [-0.025679241865873337, -0.010862798430025578,...   
1  [-0.007394320797175169, -0.024833500385284424,...   
2  [-0.0018543307669460773, -0.011931090615689754...   
3  [0.020152561366558075, 0.0015350838657468557, ...   
4  [-0.01353710051625967, -0.021896764636039734, ...   

                                             summary  sentiment  
0                 The reviewer's new favorite jeans.          1  
1  The reviewer found that the run sizes were too...         -1  
2  The reviewer loves that the item is a little h...          1  
3  The size was correct and it was a good value f...          1  
4  The reviewer loves the jeans and plans to buy ...          1

In [41]:
columns_to_drop = [
    'silhouette', 'silhouette mapping', 'proportion_or_fit', 
    'proportion_or_fit mapping', 'detail', 'detail mapping', 
    'color', 'color mapping', 'print_or_pattern', 
    'print_or_pattern mapping', 'fabric', 'fabric mapping'
]

In [42]:
summarized_df = df.drop(columns=columns_to_drop)

In [43]:
summarized_df

SKU_number               headline  rating  \
0       100001                  Jeans       5   
1       100001              Run small       1   
2       100001              Love them       5   
3       100001              Good buy!       5   
4       100001                    Fit       5   
..         ...                    ...     ...   
69      100004    Great fitting jeans       5   
70      100004             Nice jeans       4   
71      100004  Trendy & comfortable!       5   
72      100004               Perfect!       5   
73      100004             No stretch       2   

                                             comments          Dept  \
0                                  New favorite jeans  WOMENS DENIM   
1   Run sizes too small. Tons of old navy.. always...  WOMENS DENIM   
2   I love they are a little heavy and they keep y...  WOMENS DENIM   
3         Size was correct, good value for the price!  WOMENS DENIM   
4   Best jeans. Perfect fit!! Love them. Will defi...  WOMENS DENIM   
..                                                ...           ...   
69  I love these jeans. They are not too tight and...  WOMENS DENIM   
70                             snug at waist for size  WOMENS DENIM   
71                 Very flattering, love the stretch!  WOMENS DENIM   
72  Love these jeans! They're the perfect rise and...  WOMENS DENIM   
73          These jeans were long and had no stretch.  WOMENS DENIM   

                                            embedding  \
0   [-0.025679241865873337, -0.010862798430025578,...   
1   [-0.007394320797175169, -0.024833500385284424,...   
2   [-0.0018543307669460773, -0.011931090615689754...   
3   [0.020152561366558075, 0.0015350838657468557, ...   
4   [-0.01353710051625967, -0.021896764636039734, ...   
..                                                ...   
69  [-0.025672703981399536, -0.015896756201982498,...   
70  [-0.013290376402437687, 0.0037171936128288507,...   
71  [-0.03374762833118439, -0.00990808941423893, -...   
72  [-0.015251204371452332, -0.021138090640306473,...   
73  [-0.01590544916689396, -0.013450589030981064, ...   

                                              summary  sentiment  
0                  The reviewer's new favorite jeans.          1  
1   The reviewer found that the run sizes were too...         -1  
2   The reviewer loves that the item is a little h...          1  
3   The size was correct and it was a good value f...          1  
4   The reviewer loves the jeans and plans to buy ...          1  
..                                                ...        ...  
69  The reviewer loves the jeans, mentioning that ...          1  
70     The waist of the product is snug for its size.          0  
71  The review is very positive and mentions that ...          1  
72  The jeans are loved for their perfect rise and...          1  
73  The jeans were long and did not have any stretch.         -1  

[74 rows x 8 columns]

In [45]:
data_json2 = summarized_df.to_dict(orient='records')
data_json2

[{'SKU_number': 100001,
  'headline': 'Jeans',
  'rating': 5,
  'comments': 'New favorite jeans',
  'Dept': 'WOMENS DENIM',
  'embedding': [-0.025679241865873337,
   -0.010862798430025578,
   -0.002501813927665353,
   -0.019210821017622948,
   -0.022257070988416672,
   0.01624234765768051,
   -0.017629362642765045,
   -0.03870682045817375,
   0.0025082954671233892,
   -0.022944098338484764,
   0.01644975133240223,
   0.0010572756873443723,
   -0.0025228785816580057,
   -0.01823861338198185,
   -0.026327379047870636,
   0.010344288311898708,
   0.03544020652770996,
   -0.001598471193574369,
   0.02610701322555542,
   -0.01880897581577301,
   -0.006714713294059038,
   0.004536968655884266,
   -0.004219380673021078,
   -0.02924400195479393,
   -0.004374933894723654,
   -0.004682799801230431,
   0.012923878617584705,
   -0.007259149570018053,
   -0.009534114971756935,
   0.002594173653051257,
   0.02188115008175373,
   0.00384021969512105,
   -0.008348021656274796,
   -0.021103383973240852

In [47]:
from azure.cosmos import CosmosClient, PartitionKey
import uuid
# Your Cosmos DB credentials
url = "https://gapcosmosdbprlnj01.documents.azure.com:443/"
key = "001c6Nscqk9nmVP1dLzlmZ3RMpAchSayxUOfpu4BKcr1tUkR486TCtUhdCnwyjJMiFsNTkEpZD6CACDbdYfNIQ=="
database_name = "gapprojectdatabase"
container_name = "gapprojectcontainer2"
    

# Initialize the Cosmos client
client = CosmosClient(url, credential=key)

# Create a database and a container if they don't exist
database = client.create_database_if_not_exists(id=database_name)
container = database.create_container_if_not_exists(
    id=container_name,
    partition_key=PartitionKey(path='/headline'),  
    offer_throughput=400
)

for data in data_json2:
    data['id'] = str(uuid.uuid4())  # Generate a unique id
    container.create_item(body=data)

print("Data inserted successfully")

Data inserted successfully
